### IMPORT LIBRARIES

In [1]:
import pandas as pd
import numpy as np
import requests
import json
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib as mpl

colors = sns.color_palette('husl')[0:5]

import plotly
import plotly.express as px
import plotly.graph_objects as go

from dash import dcc
from dash import html
import dash_bootstrap_components as dbc
from dash.dependencies import Input, Output, State
from dash import dash_table
from dash.dash_table.Format import Format, Group, Symbol


colors = sns.color_palette('husl')[0:5]

# Обязательно
from functools import reduce
import datetime as dt
from datetime import date
import calendar

### LOAD DATA

In [2]:
secret_key = "PRapJb5XWG7s1eF2BlnaWNkdu8kfS317gy3b5w7DYcZgoIw0j13UHDw1vbrJUwQiLaecYSPIdQ6NJ2JBt3xmLLiKKlg07sxfaqI5QCKq7iTtnVUdXo2g2K1qvy6qYbvl"
account_name = "kt-on-line"

In [3]:
CREATED_FROM = '2022-07-01'

### Экспорт заказов

In [4]:
# Запрос на получение данных
deals_requests = requests.get(
    'https://kt-on-line.getcourse.ru/pl/api/account/deals?',
    params={
        'created_at[from]': CREATED_FROM,
        'key': secret_key,
    }
)
# Извлечение id запроса
deals_export_id = deals_requests.json()['info']['export_id']

In [8]:
# Получение данных
get_DEALS = requests.get(
    f'https://kt-on-line.getcourse.ru/pl/api/account/exports/{deals_export_id}?',
    params={
        'key': secret_key,
    },
)
json_DEALS = get_DEALS.json()
json_DEALS

{'success': True,
 'info': {'fields': ['ID заказа',
   'Номер',
   'ID пользователя',
   'Пользователь',
   'Email',
   'Телефон',
   'Дата создания',
   'Дата оплаты',
   'Title',
   'Статус',
   'Стоимость, RUB',
   'Оплачено',
   'Комиссия платежной системы',
   'Получено',
   'Налог',
   'Осталось после вычета комиссии платежной системы и налога',
   'Другие комиссии',
   'Заработано',
   'Валюта',
   'Менеджер',
   'Город',
   'Платежная система',
   'ID партнера',
   'Использован промокод',
   'Промоакция',
   'Комментарий к заказу',
   'Имя и Фамилия получателя сертификата',
   'Какую задачу вы хотите решить с помощью курса?',
   'Какую задачу вы хотите решить с помощью челленджа?',
   'GA_CID',
   'custom_order_id',
   'custom_utm_source',
   'custom_utm_medium',
   'custom_utm_campaign',
   'custom_utm_content',
   'custom_utm_term',
   'Вопрос пользователя',
   'К какой категории ЦА относится?',
   'Другое - К какой категории ЦА относится?',
   'Выявление потребности. Прописа

In [9]:
df = pd.DataFrame(json_DEALS)
df["info"].loc["fields"]
df["info"].loc["items"]

deals_df =pd.DataFrame(data=df["info"].loc["items"], columns=df["info"].loc["fields"])

deals_df = deals_df.replace(r'^\s*$', np.nan, regex=True)
deals_df = deals_df.replace({'-': np.nan})
deals_df['Title'] = deals_df['Title'].str.replace(r'«', '"')
deals_df['Title'] = deals_df['Title'].str.replace(r'»', '"')


deals_df['Дата создания'] = pd.to_datetime(deals_df['Дата создания'])
deals_df['Дата оплаты'] = pd.to_datetime(deals_df['Дата оплаты'])


money_in_deals = ['Стоимость, RUB',
                  'Оплачено',
                  'Комиссия платежной системы',
                  'Получено',
                  'Налог',
                  'Осталось после вычета комиссии платежной системы и налога',
                  'Другие комиссии',
                  'Заработано']


deals_df[money_in_deals] = deals_df[money_in_deals].astype(float)

# СОЗДАНИЕ ПРИЗНАКА ТИП ЗАКАЗА

# Разделение по наличию менеджера
deals_df.loc[deals_df['Менеджер'].notna(), 'type_of_transaction'] = 'Обработан отделом продаж'

deals_df.loc[deals_df['Менеджер'].isna(), 'type_of_transaction'] = 'Автооплата'

deals_df.loc[deals_df['Теги'].str.contains('снят МОП', case=False, na=False), 'type_of_transaction'] = 'Автооплата'

# Заказ без менеджера
deals_df.loc[((deals_df['Статус'] == 'Новый') |
              (deals_df['Статус'] == 'В работе') |
              (deals_df['Статус'] == 'Ожидаем оплаты') |
              (deals_df['Статус'] == 'Отложен') |
              (deals_df['Статус'] == 'Не подтвержден')) &
             (deals_df['Менеджер'].isna()), 'type_of_transaction'] = 'Заказ без менеджера'

deals_df.tail()

ID заказа   Номер ID пользователя       Пользователь  \
26294  222824844  520475       259523953               Анна   
26295  222825580  520476        78461475    Мария Левочкина   
26296  222826341  520477       249707902     Елена Куликова   
26297  222827851  520478       258831387  Горбунова Евгения   
26298  222828536  520479       235190854               Юлия   

                             Email       Телефон       Дата создания  \
26294    Anna.grishina@hotmail.com   79037230308 2022-07-25 06:26:14   
26295                  a_lev@bk.ru  +79092511821 2022-07-25 06:38:55   
26296  elenakulikova2211@gmail.com   79069348422 2022-07-25 06:51:05   
26297          Mutovina_ea@mail.ru   79835858433 2022-07-25 07:09:17   
26298          Svetova1313@mail.ru   79503516553 2022-07-25 07:17:33   

              Дата оплаты                                              Title  \
26294 2022-07-25 06:29:19  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
26295                 NaT  Участники практикума 13-14 июля 2022 г. День 2...   
26296                 NaT  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
26297                 NaT  Онлайн-интенсив "Учусь у Андрея Курпатова" | Т...   
26298                 NaT              Вирусный скрипт - приглашение друзей    

         Статус  ...  user_utm_source  user_utm_medium  \
26294  Завершен  ...              NaN              NaN   
26295  Завершен  ...        instagram          taplink   
26296     Новый  ...              AVK               tg   
26297  Завершен  ...        instagram              NaN   
26298  Завершен  ...         facebook              cpc   

                                user_utm_campaign  user_utm_content  \
26294                                         NaN               NaN   
26295                                         NaN               NaN   
26296                                        post               NaN   
26297                                  learning_2        taplink_fk   
26298  nadya_web2502_web_25-02n_23849923451410109       2_lenta_gal   

          user_utm_term  user_utm_group  user_gcpc  Теги  \
26294               NaN             NaN        NaN    []   
26295               NaN             NaN        NaN    []   
26296            MK1705             NaN        NaN    []   
26297               NaN             NaN        NaN    []   
26298  psih_ru_20-02_3l             NaN        NaN    []   

                                        Теги предложений  type_of_transaction  
26294  [*Доступ к курсу, *Оплата курса, *Худеем вмест...           Автооплата  
26295                                                 []           Автооплата  
26296  [*Доступ к курсу, *Оплата курса, *Худеем вмест...  Заказ без менеджера  
26297  [*Исключать из статистики Отдел продаж, *Тариф...           Автооплата  
26298     [softskills, вирусный скрипт, ООО Гетпродакшн]           Автооплата  

[5 rows x 66 columns]

In [10]:
sales_dep_df = deals_df.loc[deals_df['Менеджер'].notna()]
sales_dep_df

ID заказа   Номер ID пользователя         Пользователь  \
13     216234803  493746       234759811       Марат Ирсыбаев   
16     216247690  493749       256337468                ольга   
20     216259898  493754       143888155      Изабелла Инсаль   
23     216276220  493757       138170951      Артем Шмаргунов   
27     216280416  493761       120803587  Светлана Каневсккая   
...          ...     ...             ...                  ...   
26253  222792202  520434       145981947   Irina Stadnichenko   
26257  222794817  520438       259504267                Павел   
26258  222795802  520439       241796272          Иван Павлов   
26274  222807724  520455       259512145                Rimma   
26275  222810953  520456       259135637    Mariia Muzychenko   

                           Email        Телефон       Дата создания  \
13        ooo-sk-strelok@mail.ru    79899241135 2022-07-01 08:02:48   
16         kropinaolga@yandex.ru   +79218797380 2022-07-01 09:01:24   
20      Izabellainsall@gmail.com  +972526244017 2022-07-01 09:54:40   
23       Artshmargunov@gmail.com    79068660437 2022-07-01 11:24:48   
27              ssbunova@mail.ru   +79175902494 2022-07-01 11:49:38   
...                          ...            ...                 ...   
26253      Irinamarci9@gmail.com    +4748401535 2022-07-24 22:09:33   
26257         pavemick@gmail.com   +37129117884 2022-07-24 22:26:26   
26258       vaanatwork@yandex.ru    79256661405 2022-07-24 22:28:28   
26274  rimmapinkovskaa@gmail.com   380990216582 2022-07-25 00:00:22   
26275         tuchusya@gmail.com     0953238394 2022-07-25 00:20:07   

              Дата оплаты                                              Title  \
13    2022-07-01 17:06:42  АСБ_ВК_Векторное кольцо. Полный тариф "Автоном...   
16                    NaT  АС_Построить здоровые отношения и стать пример...   
20                    NaT  КТ_Обновленный курс Красная таблетка ONLINE | ...   
23                    NaT  ВШ_Кураторская поддержка. Сила мозга. Красная ...   
27    2022-07-05 19:56:45  АС_Онлайн-курсы Академии смысла. Мозг и бизнес...   
...                   ...                                                ...   
26253                 NaT  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
26257                 NaT  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
26258                 NaT  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
26274                 NaT  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
26275                 NaT  Онлайн-интенсив "Учусь у Андрея Курпатова" | Т...   

         Статус  ...     user_utm_source   user_utm_medium  \
13     Завершен  ...                 NaN               NaN   
16     В работе  ...            telegram               NaN   
20      Отменен  ...             youtube          instream   
23     В работе  ...           instagram      step_on_line   
27     Завершен  ...           instagram           taplink   
...         ...  ...                 ...               ...   
26253     Новый  ...             youtube  live0902_post_av   
26257     Новый  ...                 NaN               NaN   
26258     Новый  ...                 NaN               NaN   
26274     Новый  ...                 NaN               NaN   
26275     Новый  ...  efir_19_learning_2               NaN   

             user_utm_campaign   user_utm_content  user_utm_term  \
13                         NaN                NaN            NaN   
16             promotion_june2                 hp            NaN   
20                 12160012442       494224123150   116571752843   
23     03.01.2021_stop_trevoga  07.01.2021_shapka            NaN   
27           подробнее_о_курсе                NaN            NaN   
...                        ...                ...            ...   
26253                      NaN                NaN            NaN   
26257                      NaN                NaN            NaN   
26258                      NaN                NaN      

In [11]:
sales_dep_df['Статус'].unique()

array(['Завершен', 'В работе', 'Отменен', 'Ожидаем оплаты',
       'Частично оплачен', 'Отложен', 'Новый'], dtype=object)

In [12]:
# Каким менеджерам достались заказы
sales_dep_df.groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
    agg(taken_to_work =('ID заказа', 'count'))

taken_to_work
Дата создания Менеджер                          
2022-07-01    Анастасия Чистякова              1
              Мария Филиппенкова               1
              Олеся Спидченко                  1
              Павел Шувалов                    4
              Татьяна Сарапулова               1
...                                          ...
2022-07-24    Павел Шувалов                    5
              Татьяна Лемтюгова               14
              Татьяна Сарапулова               8
2022-07-25    Анастасия Чистякова              1
              Мария Филиппенкова               1

[136 rows x 1 columns]

In [13]:
sales_dep_df.loc[sales_dep_df['Статус'] == 'В работе'].\
    groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
    agg(in_work =('ID заказа', 'count'))

in_work
Дата создания Менеджер                    
2022-07-01    Олеся Спидченко            1
              Павел Шувалов              3
2022-07-02    Анастасия Чистякова        2
              Мария Филиппенкова         5
              Павел Шувалов              4
...                                    ...
2022-07-23    Татьяна Лемтюгова          6
              Татьяна Сарапулова         3
2022-07-24    Олеся Спидченко            6
              Татьяна Лемтюгова          2
              Татьяна Сарапулова         4

[103 rows x 1 columns]

In [14]:
def orders_by_managers(data_frame = sales_dep_df):

    taken_to_work =  data_frame.groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
           agg(taken_to_work =('ID заказа', 'count')).reset_index()

    in_work = data_frame.loc[(data_frame['Статус'] == 'В работе') |
                             (data_frame['Статус'] == 'Отложен')].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
        agg(in_work =('ID заказа', 'count')).reset_index()

    awaiting_payment = data_frame.loc[data_frame['Статус'] == 'Ожидаем оплаты'].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
        agg(awaiting_payment =('ID заказа', 'count')).reset_index()

    cancelled_orders = data_frame.loc[data_frame['Статус'] == 'Отменен'].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
        agg(cancelled_orders =('ID заказа', 'count')).reset_index()

    paid = data_frame.loc[(data_frame['Статус'] == 'Завершен')|
                          (data_frame['Статус'] == 'Частично оплачен')].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Менеджер']).\
        agg(paid =('ID заказа', 'count')).reset_index()

    data_frames_for_merging = [taken_to_work, in_work, awaiting_payment, cancelled_orders, paid]

    orders_by_managers_df = reduce(lambda  left,right: pd.merge(left,right,on=['Дата создания', 'Менеджер'],
                                                how='outer'), data_frames_for_merging)
    orders_by_managers_df.fillna(0, inplace=True)

    return orders_by_managers_df

In [15]:
orders_by_managers()

Дата создания             Менеджер  taken_to_work  in_work  \
0      2022-07-01  Анастасия Чистякова              1      0.0   
1      2022-07-01   Мария Филиппенкова              1      0.0   
2      2022-07-01      Олеся Спидченко              1      1.0   
3      2022-07-01        Павел Шувалов              4      3.0   
4      2022-07-01   Татьяна Сарапулова              1      0.0   
..            ...                  ...            ...      ...   
131    2022-07-24        Павел Шувалов              5      0.0   
132    2022-07-24    Татьяна Лемтюгова             14      2.0   
133    2022-07-24   Татьяна Сарапулова              8      4.0   
134    2022-07-25  Анастасия Чистякова              1      0.0   
135    2022-07-25   Мария Филиппенкова              1      0.0   

     awaiting_payment  cancelled_orders  paid  
0                 0.0               0.0   1.0  
1                 0.0               0.0   1.0  
2                 0.0               0.0   0.0  
3                 0.0               0.0   1.0  
4                 0.0               1.0   0.0  
..                ...               ...   ...  
131               0.0               0.0   1.0  
132               5.0               0.0   7.0  
133               0.0               0.0   3.0  
134               0.0               0.0   0.0  
135               0.0               0.0   0.0  

[136 rows x 7 columns]

In [16]:
def orders_by_offers(data_frame = sales_dep_df):

    taken_to_work =  data_frame.groupby([pd.Grouper(key='Дата создания', freq='D'), 'Title']).\
           agg(taken_to_work =('ID заказа', 'count')).reset_index()

    in_work = data_frame.loc[(data_frame['Статус'] == 'В работе') |
                             (data_frame['Статус'] == 'Отложен')].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Title']).\
        agg(in_work =('ID заказа', 'count')).reset_index()

    awaiting_payment = data_frame.loc[data_frame['Статус'] == 'Ожидаем оплаты'].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Title']).\
        agg(awaiting_payment =('ID заказа', 'count')).reset_index()

    cancelled_orders = data_frame.loc[data_frame['Статус'] == 'Отменен'].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Title']).\
        agg(cancelled_orders =('ID заказа', 'count')).reset_index()

    paid = data_frame.loc[(data_frame['Статус'] == 'Завершен')|
                          (data_frame['Статус'] == 'Частично оплачен')].\
        groupby([pd.Grouper(key='Дата создания', freq='D'), 'Title']).\
        agg(paid =('ID заказа', 'count')).reset_index()

    data_frames_for_merging = [taken_to_work, in_work, awaiting_payment, cancelled_orders, paid]

    orders_by_offers_df = reduce(lambda  left,right: pd.merge(left,right,on=['Дата создания', 'Title'],
                                                how='outer'), data_frames_for_merging)
    orders_by_offers_df.fillna(0, inplace=True)

    return orders_by_offers_df

In [17]:
orders_by_offers()

Дата создания                                              Title  \
0      2022-07-01  АС_Онлайн-курсы Академии смысла. Мозг и бизнес...   
1      2022-07-01  АС_Онлайн-курсы Академии смысла. Челлендж "Пер...   
2      2022-07-01  АС_Получить максимальный результат во всех сфе...   
3      2022-07-01  АС_Построить здоровые отношения и стать пример...   
4      2022-07-01  АСБ_ВК_Векторное кольцо. Полный тариф "Автоном...   
..            ...                                                ...   
204    2022-07-24  Онлайн-интенсив "Учусь у Андрея Курпатова" | Т...   
205    2022-07-24  Онлайн-интенсив "Учусь у Андрея Курпатова" | Т...   
206    2022-07-24                      ШШ_Мини-курс "Стоп, тревога!"   
207    2022-07-25  МХ_ "Марафон "Худеем с Андреем Курпатовым". По...   
208    2022-07-25  Онлайн-интенсив "Учусь у Андрея Курпатова" | Т...   

     taken_to_work  in_work  awaiting_payment  cancelled_orders  paid  
0                1      0.0               0.0               0.0   1.0  
1                1      1.0               0.0               0.0   0.0  
2                1      1.0               0.0               0.0   0.0  
3                1      1.0               0.0               0.0   0.0  
4                1      0.0               0.0               0.0   1.0  
..             ...      ...               ...               ...   ...  
204              7      0.0               0.0               0.0   3.0  
205              4      0.0               0.0               0.0   4.0  
206              1      0.0               0.0               0.0   1.0  
207              1      0.0               0.0               0.0   0.0  
208              1      0.0               0.0               0.0   0.0  

[209 rows x 7 columns]

In [ ]:
# Тут использовать дату оплаты
# Брать оплаченые заказы при
average_bill = sales_dep_df.groupby([pd.Grouper(key='Дата оплаты', freq='D'), 'Менеджер']).\
           agg(taken_to_work =('ID заказа', 'count'),
               average_bill =('Заработано', 'mean'),
               fact =('Заработано', 'sum')).reset_index()
average_bill

In [ ]:
average_bill_by_manager = average_bill.groupby('Менеджер')['average_bill'].mean().reset_index()
average_bill_by_manager['plan'] = 1000
average_bill_by_manager['date_setup_plan'] = '2022-07-01'
average_bill_by_manager['date_setup_plan'] = pd.to_datetime(average_bill_by_manager['date_setup_plan'])
average_bill_by_manager

In [ ]:
taken_to_work_manager = average_bill.groupby('Менеджер')['taken_to_work'].sum().reset_index()
taken_to_work_manager

In [ ]:
fact = orders_by_managers()
fact = fact.groupby('Менеджер')['paid'].sum().reset_index()
fact

In [ ]:
def plan_fact(data_frame = sales_dep_df):
    average_bill = data_frame.groupby([pd.Grouper(key='Дата оплаты', freq='D'), 'Менеджер']).\
           agg(taken_to_work =('ID заказа', 'count'),
               average_bill =('Заработано', 'mean'),
               fact =('Заработано', 'sum')).reset_index()

    average_bill_by_manager = average_bill.groupby('Менеджер')[['average_bill', 'fact']].mean().reset_index()
    average_bill_by_manager['plan'] = 1000000
    average_bill_by_manager['date_setup_plan'] = '2022-07-01'
    average_bill_by_manager['date_setup_plan'] = pd.to_datetime(average_bill_by_manager['date_setup_plan'])
    plan_fact_df = average_bill_by_manager

    plan_fact_df = plan_fact_df.merge(fact, on='Менеджер')
    plan_fact_df = plan_fact_df.merge(taken_to_work_manager, on='Менеджер')

    plan_fact_df['completion'] = ((plan_fact_df['fact'] * 100) / plan_fact_df['plan']).round(2)

    plan_fact_df['conversion'] = ((plan_fact_df['taken_to_work'] / plan_fact_df['fact']) * 100 ).round(2)

    plan_fact_df['today'] = pd.to_datetime(date.today())

    #факт в деньгах
    # таблица про плаирование
    plan_fact_df['day_after_plan'] = plan_fact_df['today'] - plan_fact_df['date_setup_plan']

    current_date = dt.date.today()
    plan_fact_df['days_in_month']= calendar.monthrange(current_date.year, current_date.month)[1]

# Исправить тут
#     plan_fact_df['forecast'] = (plan_fact_df['fact'] / plan_fact_df['day_after_plan'].dt.days * plan_fact_df['days_in_month'].dt.days).round(2)

    # plan_fact_df['percent_forecast'] = ((plan_fact_df['forecast'] * 100) / plan_fact_df['plan']).round(2)


    # plan_fact_df = plan_fact_df[['Менеджер','plan','average_bill','conversion','fact','completion','forecast', 'percent_forecast']]
    return plan_fact_df

In [ ]:
plan_fact()

In [ ]:
Прогноз = факт месяца / количество прошедших календарных дней * 30 календарных дней

In [ ]:
plan_fact()

In [ ]:
228/21*31

In [ ]:
DATE = '2022-07-10'

In [ ]:
plan_df = pd.DataFrame()

plan_df['manager'] = sales_dep_df['Менеджер'].unique()

for manger in plan_df['manager']:
    plan_df.loc[plan_df.manger == manger] = DATE


plan_df

In [ ]:
plan_df = pd.DataFrame()

plan_df['manager'] = sales_dep_df['Менеджер'].unique()

for manger in plan_df['manager']:
    plan_df.loc[plan_df.manger == manger] = DATE


plan_df